In [1]:
import os
import sys
import argparse
import numpy as np
import plotly.figure_factory as ff
import plotly.graph_objects as go
from plotly.subplots import make_subplots
from scipy.spatial.transform import Rotation

def time_alignment(ft, pose):    
    ft_time = ft[:, 0]
    pose_time = pose[:, 0]

    fx_interp = np.interp(pose_time, ft_time, ft[:, 1])
    fy_interp = np.interp(pose_time, ft_time, ft[:, 2])
    fz_interp = np.interp(pose_time, ft_time, ft[:, 3])
    tx_interp = np.interp(pose_time, ft_time, ft[:, 4])
    ty_interp = np.interp(pose_time, ft_time, ft[:, 5])
    tz_interp = np.interp(pose_time, ft_time, ft[:, 6])

    force_interp = np.stack([fx_interp, fy_interp, fz_interp]).T
    torque_interp = np.stack([tx_interp, ty_interp, tz_interp]).T
    return force_interp, torque_interp

def convert_rotation(pose):
    '''
    Compute theta_z in euler angle and 2D rotation matrix from pose quaternion
    '''
    r_ez, rmat = [], []
    for p in pose:
        euler = Rotation.from_quat(p[4:]).as_euler('zyx')
        theta_z = euler[0] + np.pi / 2
        cosz, sinz = np.cos(theta_z), np.sin(theta_z)
        r = np.array([[cosz, -sinz],
                        [sinz, cosz]])
        r_ez.append(theta_z)
        rmat.append(r)
    r_ez = np.stack(r_ez)
    rmat = np.stack(rmat)
    return r_ez, rmat

def rotate_force(force, rmat):
    '''
    Rotate the force into robot base frame
    '''
    rotated_fx, rotated_fy = [], []
    for f, r in zip(force, rmat):
        rotated_fx_fy = r.T @ np.array([f[0], f[1]])
        rotated_fx.append(rotated_fx_fy[0])
        rotated_fy.append(rotated_fx_fy[1])

    rotated_fx = np.stack(rotated_fx)
    rotated_fy = np.stack(rotated_fy)
    return rotated_fx, rotated_fy

def time_align_joint(joint, pose):
    joint_time = joint[:, 0]
    pose_time = pose[:, 0]
    
    jp_interp = np.interp(pose_time, joint_time, joint[:, 1])
    jv_interp = np.interp(pose_time, joint_time, joint[:, 2])
    jt_interp = np.interp(pose_time, joint_time, joint[:, 3])
    
    joint_interp = np.stack([jp_interp, jv_interp, jt_interp]).T
    return joint_interp


In [112]:
# Directory to load force/torque and pose data
data_dir = "/home/jiacheng/tmp/1_27_17_34_0/"

ft = np.loadtxt(os.path.join(data_dir, 'ft300s.txt'), delimiter=',')
pose = np.loadtxt(os.path.join(data_dir, 'pose.txt'), delimiter=',')
joint = np.loadtxt(os.path.join(data_dir, 'joint.txt'), delimiter=',')

# time align force torque
force_interp, torque_interp = time_alignment(ft, pose)
# Rotate force and torque in robot base frame
r_ez, rmat = convert_rotation(pose)
rotated_fx, rotated_fy = rotate_force(force_interp, rmat)

# time align joint
joint_interp = time_align_joint(joint, pose)

# Use relative time for plot
pose_time = pose[:, 0]
relative_time = pose_time - pose_time[0]

nstep = pose.shape[0]

In [113]:
fig = go.Figure(data=[go.Scatter(x=relative_time, y=rotated_fx, name='fx'),
                      go.Scatter(x=relative_time, y=rotated_fy, name='fy')
                     ]
               )
fig.show()

In [114]:
fig = go.Figure(data=[go.Scatter(x=relative_time, y=torque_interp[:,2], name='fw'),
                      go.Scatter(x=relative_time, y=joint_interp[:,2], name='joint_torque')])
fig.show()

In [115]:
fig = go.Figure(data=go.Scatter(x=relative_time, y=joint_interp[:,1], name='joint_vel'))
fig.show()

In [4]:
# Directory to load force/torque and pose data
data_dir_1 = "/home/jc/tmp/inertia_1_27_0_28_56/"
data_dir_2 = "/home/jc/tmp/inertia_1_27_0_22_19/"

ft_1 = np.loadtxt(os.path.join(data_dir_1, 'ft300s.txt'), delimiter=',')
pose_1 = np.loadtxt(os.path.join(data_dir_1, 'pose.txt'), delimiter=',')
joint_1 = np.loadtxt(os.path.join(data_dir_1, 'joint.txt'), delimiter=',')

# time align force torque
force_interp_1, torque_interp_1 = time_alignment(ft_1, pose_1)
# Rotate force and torque in robot base frame
r_ez_1, rmat_1 = convert_rotation(pose_1)
rotated_fx_1, rotated_fy_1 = rotate_force(force_interp_1, rmat_1)

# time align joint
joint_interp_1 = time_align_joint(joint_1, pose_1)

# Use relative time for plot
pose_time_1 = pose_1[:, 0]
relative_time_1 = pose_time_1 - pose_time_1[0]



In [5]:
ft_2 = np.loadtxt(os.path.join(data_dir_2, 'ft300s.txt'), delimiter=',')
pose_2 = np.loadtxt(os.path.join(data_dir_2, 'pose.txt'), delimiter=',')
joint_2 = np.loadtxt(os.path.join(data_dir_2, 'joint.txt'), delimiter=',')

# time align force torque
force_interp_2, torque_interp_2 = time_alignment(ft_2, pose_2)
# Rotate force and torque in robot base frame
r_ez_2, rmat_2 = convert_rotation(pose_2)
rotated_fx_2, rotated_fy_2 = rotate_force(force_interp_2, rmat_2)

# time align joint
joint_interp_2 = time_align_joint(joint_2, pose_2)

# Use relative time for plot
pose_time_2 = pose_2[:, 0]
relative_time_2 = pose_time_2 - pose_time_2[0]

In [6]:
torque_interp_2[:40,2]

array([ 0.01      ,  0.01506598,  0.0069016 , -0.00580957, -0.01626308,
       -0.00388874,  0.01258701,  0.02548469,  0.03816362,  0.03498008,
        0.02691823,  0.01433955, -0.01      , -0.01      ,  0.00226057,
        0.01519945,  0.02813378,  0.03      ,  0.03      ,  0.03      ,
        0.13920857,  0.20343699,  0.2599055 ,  0.45361584,  0.53769863,
        0.76099274,  0.85108767,  0.93969519,  1.10902951,  1.13854367,
        1.10697243,  1.04909308,  1.02349826,  1.02940223,  1.02162379,
        1.02783689,  1.02767651,  0.9763715 ,  0.91379336,  0.81      ])

In [8]:
fig = go.Figure(data=[go.Scatter(x=relative_time_1, y=torque_interp_1[:40,2], name='fw_1'),
                      go.Scatter(x=relative_time_2, y=torque_interp_2[:40,2], name='fw_2')])
fig.show()

In [10]:
fig = go.Figure(data=[go.Scatter(x=relative_time_1, y=joint_interp_1[:40,1], name='jv_1'),
                      go.Scatter(x=relative_time_2, y=joint_interp_2[:40,1], name='jv_2')])
fig.show()

In [11]:
def find_slop(x, y):
    n = np.size(x)

    x_mean = np.mean(x)
    y_mean = np.mean(y)
    x_mean,y_mean

    Sxy = np.sum(x*y)- n*x_mean*y_mean
    Sxx = np.sum(x*x)-n*x_mean*x_mean

    b1 = Sxy/Sxx
    return b1

In [18]:
slopes_1 = np.zeros(relative_time_1.shape[0])
slopes_2 = np.zeros(relative_time_2.shape[0])
win_size = 3

for i in range(relative_time_1.shape[0] - win_size):
    slopes_1[i] = find_slop(relative_time_1[i:i+win_size], joint_interp_1[i:i+win_size, 1])
for i in range(relative_time_2.shape[0] - win_size):
    slopes_2[i] = find_slop(relative_time_2[i:i+win_size], joint_interp_2[i:i+win_size, 1])
    

In [19]:
fig = go.Figure(data=[go.Scatter(x=relative_time_1, y=slopes_1[:40], name='accel_1'),
                      go.Scatter(x=relative_time_2, y=slopes_2[:40], name='accel_2')])
fig.show()

In [24]:
tau_1, tau_2 = 1.4, 1.1
accel_1, accel_2 = 16, 8

m = 6 * 0.46
I0_gt = 2 * 0.46 * (0.025**2 + 0.075**2 + 0.125**2)
Ip = (tau_1 - tau_2) / (accel_1 - accel_2)
I0 = Ip - m * 0.075**2
print(I0_gt, Ip, I0)

0.020125 0.03749999999999998 0.021974999999999977
